In [1]:
from datetime import datetime
from pathlib import Path
from dotenv import load_dotenv
import os
import os
import sys
import pandas as pd
pd.options.mode.chained_assignment = None
from pandas import json_normalize
from datetime import datetime
from pathlib import Path
import requests
from requests.exceptions import ConnectionError
import json
import time
import xmltodict
from zipfile import ZipFile
import shapely
import shapely.wkt
from shapely.ops import transform
import pyproj
import shutil
import numpy as np
os.environ['PROJ_NETWORK'] = 'OFF'

In [2]:
pd.set_option('display.max_rows', 1900)
pd.set_option('display.max_columns', 100)

In [3]:
start_time = datetime.utcnow()

# USER MUST EDIT THE ENVIRONMENT FILE REFERENCED BELOW, OR CREATE THEIR OWN FILE AND REFERENCE IT
load_dotenv('PRE.env')

# set configuration based on contents of the ENVIRONMENT FILE.
conn = {
    'domain': os.getenv("HOST"),
    'username': os.getenv("API_USER"),
    'access_token': os.getenv("API_TOKEN"),
}

# use default path to local "output" directory
#output_dir = eodslib.make_output_dir(Path.cwd() / 'output')

# specify a particular ARD to download using 'title' keyword
eods_params = {
    #'output_dir':output_dir,
    #'title':'S2B_20200424_lat55lon215_T30UWF_ORB037_utm30n_osgb_vmsk_sharp_rad_srefdem_stdsref',
    'find_least_cloud': True,
    'sat_id': 2
    }

kwargs = eods_params

# list_of_layers, df = query_catalog(conn, **eods_params)

In [4]:
params = {
        'username':conn['username'],
        'api_key':conn['access_token'],
        'offset':0,
    }

# set output path if not specified
if 'output_dir' not in kwargs:
    kwargs['output_dir']=Path.cwd()

# set limit to a sufficiently big number if not specified
if 'limit' not in kwargs:
    params.update({'limit':20000})
else:
    params.update({'limit':kwargs['limit']})

# set type to layer if "raster" or "vector" not specified
if 'type' not in kwargs:
    kwargs['type']='layer'
else:
    params.update({'type__in':kwargs['type']})

if 'verify' not in kwargs:
    kwargs['verify'] = True

if 'sat_id' in kwargs and 'find_least_cloud' in kwargs:
    if kwargs['sat_id'] == 1:            
        # throw an error if user specifies an s2 custom function with s1
        raise ValueError("QUERY failed, you have specified 'sat_id'=1 and 'find_least_cloud'=True. Use 'sat_id'=2 and 'find_least_cloud'=True")

if 'sat_id' in kwargs:
    params.update({'keywords__slug__in': 'sentinel-' + str(kwargs['sat_id'])})        

# date filter condition check and set
if 'start_date' in kwargs and 'end_date' not in kwargs:
    raise ValueError("QUERY failed, if querying by date, please specify *BOTH* 'start_date' and 'end_date'")
elif 'start_date' not in kwargs and 'end_date' in kwargs:
    raise ValueError("QUERY failed, if querying by date, please specify *BOTH* 'start_date' and 'end_date'")
elif 'start_date' in kwargs and 'end_date' in kwargs:
    params.update({'date__range': kwargs['start_date'] + ' 00:00,' + kwargs['end_date'] + ' 00:00'})

if 'title' in kwargs:
    params.update({'q': kwargs['title']})

if 'geom' in kwargs:
    params.update({'geometry': kwargs['geom']})

# cloud filter condition check and set    
if 'cloud_min' in kwargs and 'cloud_max' not in kwargs:
    raise ValueError("QUERY failed, if querying by cloud cover, please specify *BOTH* 'cloud_min' and 'cloud_max'")
elif 'cloud_min' not in kwargs and 'cloud_max' in kwargs:
    raise ValueError("QUERY failed, if querying by cloud cover, please specify *BOTH* 'cloud_min' and 'cloud_max'")
elif 'cloud_min' in kwargs and 'cloud_max' in kwargs:
    if kwargs['sat_id'] == 1:
        raise ValueError("QUERY failed, if querying by cloud cover, please specify 'sat_id'=2")
    elif kwargs['sat_id'] == 2:
        params.update({'cc_min': kwargs['cloud_min']})
        params.update({'cc_max': kwargs['cloud_max']})            

print('\n' + datetime.utcnow().isoformat() + ' :: PARAMENTERS USED = ' + str(params))


2021-07-27T15:09:42.042678 :: PARAMENTERS USED = {'username': 'admin', 'api_key': 'ndA91y6TWFBFeqjEGMhkgdBTJXLnsL', 'offset': 0, 'limit': 20000, 'keywords__slug__in': 'sentinel-2'}


In [5]:
response = requests.get(
    conn['domain'] + '/api/base/search',
    params=params,
    verify=kwargs['verify'],
    headers={'User-Agent': 'python'}
)

if response.status_code == 200:

    print(datetime.utcnow().isoformat() + ' :: RESPONSE STATUS = 200 (SUCCESS)')
    print(datetime.utcnow().isoformat() + ' :: QUERY URL USED = ' + response.url)

    # create a json object of the api payload content
    json_response = json.loads(response.content)

    if json_response['meta']['total_count'] > 0:

        df = json_normalize(json_response, 'objects')

        # add extra cols to df for s2 info
        if 'sat_id' in kwargs:
            if kwargs['sat_id'] == 2:
                df['granule-ref'] = df['title'].str.split('_',n=4).str[3]
                df['orbit-ref'] = df['title'].str.split('_',n=5).str[-2]
                df['ARCSI_CLOUD_COVER'] =df['supplemental_information'].str.split(n=6).str[5]           

2021-07-27T15:09:49.330643 :: RESPONSE STATUS = 200 (SUCCESS)
2021-07-27T15:09:49.330736 :: QUERY URL USED = https://eob-pre1.azure.defra.cloud/api/base/search/?username=admin&api_key=ndA91y6TWFBFeqjEGMhkgdBTJXLnsL&offset=0&limit=20000&keywords__slug__in=sentinel-2


In [6]:
if len(df[df['title'].str.contains('SPLIT')]) > 0:

    print(datetime.utcnow().isoformat() + ' :: INFO. Split Granules found in query results ... removing')

    # create a title substring which can be matched against a split list
    df['title_stub'] = df['title'].str.split('_T', expand=True).loc[:,0] + '_' + df['granule-ref'].str[:6]

    """# create a Series object for that only contains the title 'sub string' 
    s = df[df["title"].str.contains("SPLIT")].title.str.split('SPLIT1',expand=True).loc[:,0]

    # select rows from main dataframe where records DO NOT MATCH (~ = syntax) the 'split' series of title stub strings
    filtered_out_split = df[~df.title_stub.isin(s)]"""

2021-07-27T15:09:49.387400 :: INFO. Split Granules found in query results ... removing


In [7]:
temp_df = df[df['split_granule.name'].notna()][['alternate', 'ARCSI_CLOUD_COVER']].copy()

In [8]:
temp_df

alternate    ARCSI_CLOUD_COVER
244  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...    0.173685684800148
245  geonode:S2A_20200810_lat50lon503_T30UUA_ORB080...  0.20804637670516968
249  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...  0.14184147119522095
252  geonode:S2A_20200810_lat50lon503_T30UUASPLIT1_...  0.07855145633220673
448  geonode:S2A_20200728_lat55lon213_T30UWG_ORB037...   0.9106923341751099
452  geonode:S2A_20200728_lat55lon213_T30UWGSPLIT1_...   0.6540082693099976
457  geonode:S2A_20200728_lat55lon061_T30UXF_ORB037...   0.7374271154403687
463  geonode:S2A_20200728_lat55lon215_T30UWFSPLIT1_...   0.6250476241111755
469  geonode:S2A_20200728_lat55lon215_T30UWF_ORB037...   0.7653273344039917
470  geonode:S2A_20200728_lat55lon061_T30UXFSPLIT1_...  0.30046480894088745
476  geonode:S2B_20200727_lat52lon07_T30UYC_ORB094_...   0.6763184666633606
480  geonode:S2B_20200727_lat52lon089_T31UCT_ORB094...   0.7163509130477905
484  geonode:S2B_20200727_lat52lon07_T30UYCSPLIT1_O...   0.5079259872436523
488  geonode:S2B_20200727_lat52lon089_T31UCTSPLIT1S...   0.5655169486999512
546  geonode:S2A_20200721_lat51lon364_T30UVB_ORB080...  0.14500795304775238
557  geonode:S2A_20200721_lat51lon364_T30UVBSPLIT1_...    0.451851487159729
825  geonode:S2A_20200628_lat55lon215_T30UWFSPLIT1_...   0.7955636978149414
838  geonode:S2A_20200628_lat54lon066_T30UXE_ORB037...   0.8122555613517761
839  geonode:S2A_20200628_lat55lon215_T30UWF_ORB037...   0.6726863980293274
840  geonode:S2A_20200628_lat55lon061_T30UXF_ORB037...   0.9149492979049683
844  geonode:S2A_20200628_lat54lon066_T30UXESPLIT1_...   0.8316067457199097
845  geonode:S2A_20200628_lat55lon061_T30UXFSPLIT1_...   0.9127920866012573

In [9]:
temp_df.rename(columns={"alternate": "split_granule.name", "ARCSI_CLOUD_COVER": "split_ARCSI_CLOUD_COVER"}, inplace=True)

In [10]:
temp_df

split_granule.name split_ARCSI_CLOUD_COVER
244  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...       0.173685684800148
245  geonode:S2A_20200810_lat50lon503_T30UUA_ORB080...     0.20804637670516968
249  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...     0.14184147119522095
252  geonode:S2A_20200810_lat50lon503_T30UUASPLIT1_...     0.07855145633220673
448  geonode:S2A_20200728_lat55lon213_T30UWG_ORB037...      0.9106923341751099
452  geonode:S2A_20200728_lat55lon213_T30UWGSPLIT1_...      0.6540082693099976
457  geonode:S2A_20200728_lat55lon061_T30UXF_ORB037...      0.7374271154403687
463  geonode:S2A_20200728_lat55lon215_T30UWFSPLIT1_...      0.6250476241111755
469  geonode:S2A_20200728_lat55lon215_T30UWF_ORB037...      0.7653273344039917
470  geonode:S2A_20200728_lat55lon061_T30UXFSPLIT1_...     0.30046480894088745
476  geonode:S2B_20200727_lat52lon07_T30UYC_ORB094_...      0.6763184666633606
480  geonode:S2B_20200727_lat52lon089_T31UCT_ORB094...      0.7163509130477905
484  geonode:S2B_20200727_lat52lon07_T30UYCSPLIT1_O...      0.5079259872436523
488  geonode:S2B_20200727_lat52lon089_T31UCTSPLIT1S...      0.5655169486999512
546  geonode:S2A_20200721_lat51lon364_T30UVB_ORB080...     0.14500795304775238
557  geonode:S2A_20200721_lat51lon364_T30UVBSPLIT1_...       0.451851487159729
825  geonode:S2A_20200628_lat55lon215_T30UWFSPLIT1_...      0.7955636978149414
838  geonode:S2A_20200628_lat54lon066_T30UXE_ORB037...      0.8122555613517761
839  geonode:S2A_20200628_lat55lon215_T30UWF_ORB037...      0.6726863980293274
840  geonode:S2A_20200628_lat55lon061_T30UXF_ORB037...      0.9149492979049683
844  geonode:S2A_20200628_lat54lon066_T30UXESPLIT1_...      0.8316067457199097
845  geonode:S2A_20200628_lat55lon061_T30UXFSPLIT1_...      0.9127920866012573

In [11]:
merged_df = df[df['split_granule.name'].notna()].reset_index().merge(temp_df, how='outer', on='split_granule.name').set_index('index')

In [12]:
df[df['split_granule.name'].notna()]

abstract  \
244  These data have been created by the Department...   
245  These data have been created by the Department...   
249  These data have been created by the Department...   
252  These data have been created by the Department...   
448  These data have been created by the Department...   
452  These data have been created by the Department...   
457  These data have been created by the Department...   
463  These data have been created by the Department...   
469  These data have been created by the Department...   
470  These data have been created by the Department...   
476  These data have been created by the Department...   
480  These data have been created by the Department...   
484  These data have been created by the Department...   
488  These data have been created by the Department...   
546  These data have been created by the Department...   
557  These data have been created by the Department...   
825  These data have been created by the Department...   
838  These data have been created by the Department...   
839  These data have been created by the Department...   
840  These data have been created by the Department...   
844  These data have been created by the Department...   
845  These data have been created by the Department...   

                                             alternate  \
244  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...   
245  geonode:S2A_20200810_lat50lon503_T30UUA_ORB080...   
249  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
252  geonode:S2A_20200810_lat50lon503_T30UUASPLIT1_...   
448  geonode:S2A_20200728_lat55lon213_T30UWG_ORB037...   
452  geonode:S2A_20200728_lat55lon213_T30UWGSPLIT1_...   
457  geonode:S2A_20200728_lat55lon061_T30UXF_ORB037...   
463  geonode:S2A_20200728_lat55lon215_T30UWFSPLIT1_...   
469  geonode:S2A_20200728_lat55lon215_T30UWF_ORB037...   
470  geonode:S2A_20200728_lat55lon061_T30UXFSPLIT1_...   
476  geonode:S2B_20200727_lat52lon07_T30UYC_ORB094_...   
480  geonode:S2B_20200727_lat52lon089_T31UCT_ORB094...   
484  geonode:S2B_20200727_lat52lon07_T30UYCSPLIT1_O...   
488  geonode:S2B_20200727_lat52lon089_T31UCTSPLIT1S...   
546  geonode:S2A_20200721_lat51lon364_T30UVB_ORB080...   
557  geonode:S2A_20200721_lat51lon364_T30UVBSPLIT1_...   
825  geonode:S2A_20200628_lat55lon215_T30UWFSPLIT1_...   
838  geonode:S2A_20200628_lat54lon066_T30UXE_ORB037...   
839  geonode:S2A_20200628_lat55lon215_T30UWF_ORB037...   
840  geonode:S2A_20200628_lat55lon061_T30UXF_ORB037...   
844  geonode:S2A_20200628_lat54lon066_T30UXESPLIT1_...   
845  geonode:S2A_20200628_lat55lon061_T30UXFSPLIT1_...   

                      category   category__gn_description  cloud_cover  \
244  imagerybasemapsearthcover  imagerybasemapsearthcover         17.0   
245  imagerybasemapsearthcover  imagerybasemapsearthcover         21.0   
249  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   
252  imagerybasemapsearthcover  imagerybasemapsearthcover          8.0   
448  imagerybasemapsearthcover  imagerybasemapsearthcover         91.0   
452  imagerybasemapsearthcover  imagerybasemapsearthcover         65.0   
457  imagerybasemapsearthcover  imagerybasemapsearthcover         74.0   
463  imagerybasemapsearthcover  imagerybasemapsearthcover         63.0   
469  imagerybasemapsearthcover  imagerybasemapsearthcover         77.0   
470  imagerybasemapsearthcover  imagerybasemapsearthcover         30.0   
476  imagerybasemapsearthcover  imagerybasemapsearthcover         68.0   
480  imagerybasemapsearthcover  imagerybasemapsearthcover         72.0   
484  imagerybasemapsearthcover  imagerybasemapsearthcover         51.0   
488  imagerybasemapsearthcover  imagerybasemapsearthcover         57.0   
546  imagerybasemapsearthcover  imagerybasemapsearthcover         15.0   
557  imagerybasemapsearthcover  imagerybasemapsearthcover         45.0   
825  imagerybasemapsearthcover  imagerybasemapsearthcover         80.0   
838  imagerybasemapsearthcover  imagerybasem

In [13]:
df['split_ARCSI_CLOUD_COVER'] = np.nan

In [14]:
df.loc[df['split_granule.name'].notna(), 'split_ARCSI_CLOUD_COVER'] = merged_df['split_ARCSI_CLOUD_COVER']

In [15]:
df

abstract  \
0    These data have been created by the Department...   
1    These data have been created by the Department...   
2    These data have been created by the Department...   
3    These data have been created by the Department...   
4    These data have been created by the Department...   
5    These data have been created by the Department...   
6    These data have been created by the Department...   
7    These data have been created by the Department...   
8    These data have been created by the Department...   
9    These data have been created by the Department...   
10   These data have been created by the Department...   
11   These data have been created by the Department...   
12   These data have been created by the Department...   
13   These data have been created by the Department...   
14   These data have been created by the Department...   
15   These data have been created by the Department...   
16   These data have been created by the Department...   
17   These data have been created by the Department...   
18   These data have been created by the Department...   
19   These data have been created by the Department...   
20   These data have been created by the Department...   
21   These data have been created by the Department...   
22   These data have been created by the Department...   
23   These data have been created by the Department...   
24   These data have been created by the Department...   
25   These data have been created by the Department...   
26   These data have been created by the Department...   
27   These data have been created by the Department...   
28   These data have been created by the Department...   
29   These data have been created by the Department...   
30   These data have been created by the Department...   
31   These data have been created by the Department...   
32   These data have been created by the Department...   
33   These data have been created by the Department...   
34   These data have been created by the Department...   
35   These data have been created by the Department...   
36   These data have been created by the Department...   
37   These data have been created by the Department...   
38   These data have been created by the Department...   
39   These data have been created by the Department...   
40   These data have been created by the Department...   
41   These data have been created by the Department...   
42   These data have been created by the Department...   
43   These data have been created by the Department...   
44   These data have been created by the Department...   
45   These data have been created by the Department...   
46   These data have been created by the Department...   
47   These data have been created by the Department...   
48   These data have been created by the Department...   
49   These data have been created by the Department...   
50   These data have been created by the Department...   
51   These data have been created by the Department...   
52   These data have been created by the Department...   
53   These data have been created by the Department...   
54   These data have been created by the Department...   
55   These data have been created by the Department...   
56   These data have been created by the Department...   
57   These data have been created by the Department...   
58   These data have been created by the Department...   
59   These data have been created by the Department...   
60   These data have been created by the Department...   
61   These data have been created by the Department...   
62   These data have been created by the Department...   
63   These data have been created by the Department...   
64   These data have been created by the Department...   
65   These data have been created by the Department...   
66   These data have been created by the Department...   
67   These data have been created by the Department...   
68   These data have been created by the Dep

In [16]:
df.loc[df['id']==9281, 'ARCSI_CLOUD_COVER'] = '0.2'
df.loc[df['id']==9117, 'ARCSI_CLOUD_COVER'] = '0.2'

In [17]:
split_cloud_cover = np.where(df['split_granule.name'].notna(), ((df['ARCSI_CLOUD_COVER'].astype(
    float) + df['split_ARCSI_CLOUD_COVER'].astype(
    float).astype(float))/2).astype(str), df['ARCSI_CLOUD_COVER'])

df['split_cloud_cover'] = split_cloud_cover

In [18]:
df

abstract  \
0    These data have been created by the Department...   
1    These data have been created by the Department...   
2    These data have been created by the Department...   
3    These data have been created by the Department...   
4    These data have been created by the Department...   
5    These data have been created by the Department...   
6    These data have been created by the Department...   
7    These data have been created by the Department...   
8    These data have been created by the Department...   
9    These data have been created by the Department...   
10   These data have been created by the Department...   
11   These data have been created by the Department...   
12   These data have been created by the Department...   
13   These data have been created by the Department...   
14   These data have been created by the Department...   
15   These data have been created by the Department...   
16   These data have been created by the Department...   
17   These data have been created by the Department...   
18   These data have been created by the Department...   
19   These data have been created by the Department...   
20   These data have been created by the Department...   
21   These data have been created by the Department...   
22   These data have been created by the Department...   
23   These data have been created by the Department...   
24   These data have been created by the Department...   
25   These data have been created by the Department...   
26   These data have been created by the Department...   
27   These data have been created by the Department...   
28   These data have been created by the Department...   
29   These data have been created by the Department...   
30   These data have been created by the Department...   
31   These data have been created by the Department...   
32   These data have been created by the Department...   
33   These data have been created by the Department...   
34   These data have been created by the Department...   
35   These data have been created by the Department...   
36   These data have been created by the Department...   
37   These data have been created by the Department...   
38   These data have been created by the Department...   
39   These data have been created by the Department...   
40   These data have been created by the Department...   
41   These data have been created by the Department...   
42   These data have been created by the Department...   
43   These data have been created by the Department...   
44   These data have been created by the Department...   
45   These data have been created by the Department...   
46   These data have been created by the Department...   
47   These data have been created by the Department...   
48   These data have been created by the Department...   
49   These data have been created by the Department...   
50   These data have been created by the Department...   
51   These data have been created by the Department...   
52   These data have been created by the Department...   
53   These data have been created by the Department...   
54   These data have been created by the Department...   
55   These data have been created by the Department...   
56   These data have been created by the Department...   
57   These data have been created by the Department...   
58   These data have been created by the Department...   
59   These data have been created by the Department...   
60   These data have been created by the Department...   
61   These data have been created by the Department...   
62   These data have been created by the Department...   
63   These data have been created by the Department...   
64   These data have been created by the Department...   
65   These data have been created by the Department...   
66   These data have been created by the Department...   
67   These data have been created by the Department...   
68   These data have been created by the Dep

In [19]:
no_split_df = df[~df['title'].str.contains("SPLIT")]

In [20]:
no_split_df[no_split_df['granule-ref'] == 'T29UQR']

abstract  \
7    These data have been created by the Department...   
74   These data have been created by the Department...   
126  These data have been created by the Department...   
171  These data have been created by the Department...   
200  These data have been created by the Department...   
249  These data have been created by the Department...   
303  These data have been created by the Department...   
333  These data have been created by the Department...   
362  These data have been created by the Department...   
446  These data have been created by the Department...   
551  These data have been created by the Department...   
620  These data have been created by the Department...   
640  These data have been created by the Department...   
669  These data have been created by the Department...   
740  These data have been created by the Department...   
807  These data have been created by the Department...   
821  These data have been created by the Department...   

                                             alternate  \
7    geonode:S2A_20210726_lat50lon544_T29UQR_ORB080...   
74   geonode:S2B_20210721_lat50lon544_T29UQR_ORB080...   
126  geonode:S2B_20210718_lat50lon544_T29UQR_ORB037...   
171  geonode:S2B_20201004_lat50lon544_T29UQR_ORB080...   
200  geonode:S2B_20200914_lat50lon544_T29UQR_ORB080...   
249  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
303  geonode:S2A_20200807_lat50lon544_T29UQR_ORB037...   
333  geonode:S2B_20200805_lat50lon544_T29UQR_ORB080...   
362  geonode:S2B_20200802_lat50lon544_T29UQR_ORB037...   
446  geonode:S2A_20200728_lat50lon544_T29UQR_ORB037...   
551  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   
620  geonode:S2B_20200716_lat50lon544_T29UQR_ORB080...   
640  geonode:S2B_20200713_lat50lon544_T29UQR_ORB037...   
669  geonode:S2A_20200711_lat50lon544_T29UQR_ORB080...   
740  geonode:S2B_20200706_lat50lon544_T29UQR_ORB080...   
807  geonode:S2A_20200701_lat50lon544_T29UQR_ORB080...   
821  geonode:S2A_20200628_lat50lon544_T29UQR_ORB037...   

                      category   category__gn_description  cloud_cover  \
7    imagerybasemapsearthcover  imagerybasemapsearthcover         90.0   
74   imagerybasemapsearthcover  imagerybasemapsearthcover         21.0   
126  imagerybasemapsearthcover  imagerybasemapsearthcover          3.0   
171  imagerybasemapsearthcover  imagerybasemapsearthcover         92.0   
200  imagerybasemapsearthcover  imagerybasemapsearthcover         46.0   
249  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   
303  imagerybasemapsearthcover  imagerybasemapsearthcover         59.0   
333  imagerybasemapsearthcover  imagerybasemapsearthcover         50.0   
362  imagerybasemapsearthcover  imagerybasemapsearthcover         80.0   
446  imagerybasemapsearthcover  imagerybasemapsearthcover         42.0   
551  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   
620  imagerybasemapsearthcover  imagerybasemapsearthcover         79.0   
640  imagerybasemapsearthcover  imagerybasemapsearthcover         76.0   
669  imagerybasemapsearthcover  imagerybasemapsearthcover         13.0   
740  imagerybasemapsearthcover  imagerybasemapsearthcover         40.0   
807  imagerybasemapsearthcover  imagerybasemapsearthcover         47.0   
821  imagerybasemapsearthcover  imagerybasemapsearthcover         74.0   

    csw_type                                   csw_wkt_geometry  \
7    dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
74   dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
126  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
171  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
200  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
249  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
303  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
333  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   
362  dataset  POLYGO

In [21]:
# import safe granule-orb list
if Path(Path.cwd() / 'static' / 'safe-granule-orbit-list.txt').exists():
    df_safe_list = pd.read_csv(Path.cwd() / 'static' / 'safe-granule-orbit-list.txt')
else:
    raise ValueError('ERROR :: safe-granule-orbit-list.txt cannot be found')

# create new col that matches the granule-orbit syntax
no_split_df['gran-orb'] = no_split_df['granule-ref'].str[:6] + '_' + no_split_df['orbit-ref']
no_split_df['granule-stub'] = no_split_df['granule-ref'].str[:6]

df['gran-orb'] = df['granule-ref'].str[:6] + '_' + df['orbit-ref']
df['granule-stub'] = df['granule-ref'].str[:6]

filtered_df = pd.merge(no_split_df,df_safe_list)

"""split_cloud_cover = np.where(filtered_df['split_granule.name'].notna(), ((filtered_df['ARCSI_CLOUD_COVER'].astype(
    float) + df[df['title'] == filtered_df['split_granule.name']]['split_granule.cloud_cover'].astype(float))/2).astype(str), filtered_df['ARCSI_CLOUD_COVER'])

filtered_df['split_cloud_cover'] = split_cloud_cover"""

if len(filtered_df) > 0:
    return_df = filtered_df.sort_values("split_cloud_cover").groupby(["granule-stub"], as_index=False).nth(0).sort_values("granule-stub")

    matching_split_series = return_df[return_df['split_granule.name'].notna()]['split_granule.name']
    matching_split_df = df[df['alternate'].isin(matching_split_series)]

    # matching_split_df['split_cloud_cover'] = ((matching_split_df['ARCSI_CLOUD_COVER'].astype(float) + matching_split_df['split_granule.cloud_cover'].astype(float))/2).astype(str)

    return_df = pd.concat([return_df, matching_split_df], ignore_index=True)
    
else:
    raise ValueError('ERROR : You have selected find_lowest_cloud=True BUT your search criteria is too narrow, spatially or temporally and did not match any granule references in "./static/safe-granule-orbit-list.txt". Suggest widening your search')


In [22]:
df[df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
551  These data have been created by the Department...   

                                             alternate  \
551  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
551  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   

    csw_type                                   csw_wkt_geometry  \
551  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
551  2020-07-21T11:33:21  /layers/geonode:S2A_20200721_lat50lon544_T29UQ...   

       id                                           keywords  \
551  9281  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
551  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
551              0       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
551            NaN  EPSG:27700  raster   

                              supplemental_information  \
551  Data Collection Time: 11:33:21\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
551  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
551  S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
551  48f3bf5a-c468-421e-9ba6-124985e43ed3                        NaN   

    split_granule.name granule-ref orbit-ref ARCSI_CLOUD_COVER  \
551                NaN      T29UQR    ORB080               0.2   

                          title_stub split_ARCSI_CLOUD_COVER  \
551  S2A_20200721_lat50lon544_T29UQR                     NaN   

    split_cloud_cover       gran-orb granule-stub  
551               0.2  T29UQR_ORB080       T29UQR

In [23]:
df[df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
249  These data have been created by the Department...   

                                             alternate  \
249  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
249  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   

    csw_type                                   csw_wkt_geometry  \
249  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
249  2020-08-10T11:33:31  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...   

       id                                           keywords  \
249  9746  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
249  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
249              2       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
249            NaN  EPSG:27700  raster   

                              supplemental_information  \
249  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
249  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
249  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
249  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                    split_granule.name granule-ref orbit-ref  \
249  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

       ARCSI_CLOUD_COVER                       title_stub  \
249  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

    split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
249       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [24]:
no_split_df[no_split_df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
551  These data have been created by the Department...   

                                             alternate  \
551  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
551  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   

    csw_type                                   csw_wkt_geometry  \
551  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
551  2020-07-21T11:33:21  /layers/geonode:S2A_20200721_lat50lon544_T29UQ...   

       id                                           keywords  \
551  9281  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
551  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
551              0       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
551            NaN  EPSG:27700  raster   

                              supplemental_information  \
551  Data Collection Time: 11:33:21\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
551  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
551  S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
551  48f3bf5a-c468-421e-9ba6-124985e43ed3                        NaN   

    split_granule.name granule-ref orbit-ref ARCSI_CLOUD_COVER  \
551                NaN      T29UQR    ORB080               0.2   

                          title_stub split_ARCSI_CLOUD_COVER  \
551  S2A_20200721_lat50lon544_T29UQR                     NaN   

    split_cloud_cover       gran-orb granule-stub  
551               0.2  T29UQR_ORB080       T29UQR

In [25]:
no_split_df[no_split_df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
249  These data have been created by the Department...   

                                             alternate  \
249  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
249  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   

    csw_type                                   csw_wkt_geometry  \
249  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
249  2020-08-10T11:33:31  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...   

       id                                           keywords  \
249  9746  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
249  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
249              2       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
249            NaN  EPSG:27700  raster   

                              supplemental_information  \
249  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
249  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
249  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
249  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                    split_granule.name granule-ref orbit-ref  \
249  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

       ARCSI_CLOUD_COVER                       title_stub  \
249  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

    split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
249       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [26]:
filtered_df[filtered_df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
15  These data have been created by the Department...   

                                            alternate  \
15  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   

                     category   category__gn_description  cloud_cover  \
15  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   

   csw_type                                   csw_wkt_geometry  \
15  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                   date                                         detail_url  \
15  2020-07-21T11:33:21  /layers/geonode:S2A_20200721_lat50lon544_T29UQ...   

      id                                           keywords  \
15  9281  [analysis-ready-data, earth-observation, satel...   

                                             location owner__username  \
15  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

    popular_count  rating                   regions  share_count  \
15              0       0  [Europe, United Kingdom]            0   

    split_granule        srid subtype  \
15            NaN  EPSG:27700  raster   

                             supplemental_information  \
15  Data Collection Time: 11:33:21\nARCSI_CLOUD_CO...   

                                        thumbnail_url  \
15  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                title   type  \
15  S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                    uuid  split_granule.cloud_cover  \
15  48f3bf5a-c468-421e-9ba6-124985e43ed3                        NaN   

   split_granule.name granule-ref orbit-ref ARCSI_CLOUD_COVER  \
15                NaN      T29UQR    ORB080               0.2   

                         title_stub split_ARCSI_CLOUD_COVER split_cloud_cover  \
15  S2A_20200721_lat50lon544_T29UQR                     NaN               0.2   

         gran-orb granule-stub  
15  T29UQR_ORB080       T29UQR

In [27]:
filtered_df[filtered_df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
13  These data have been created by the Department...   

                                            alternate  \
13  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                     category   category__gn_description  cloud_cover  \
13  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   

   csw_type                                   csw_wkt_geometry  \
13  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                   date                                         detail_url  \
13  2020-08-10T11:33:31  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...   

      id                                           keywords  \
13  9746  [analysis-ready-data, earth-observation, satel...   

                                             location owner__username  \
13  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

    popular_count  rating                   regions  share_count  \
13              2       0  [Europe, United Kingdom]            0   

    split_granule        srid subtype  \
13            NaN  EPSG:27700  raster   

                             supplemental_information  \
13  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                        thumbnail_url  \
13  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                title   type  \
13  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                    uuid  split_granule.cloud_cover  \
13  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                   split_granule.name granule-ref orbit-ref  \
13  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

      ARCSI_CLOUD_COVER                       title_stub  \
13  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

   split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
13       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [28]:
return_df[return_df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

Empty DataFrame
Columns: [abstract, alternate, category, category__gn_description, cloud_cover, csw_type, csw_wkt_geometry, date, detail_url, id, keywords, location, owner__username, popular_count, rating, regions, share_count, split_granule, srid, subtype, supplemental_information, thumbnail_url, title, type, uuid, split_granule.cloud_cover, split_granule.name, granule-ref, orbit-ref, ARCSI_CLOUD_COVER, title_stub, split_ARCSI_CLOUD_COVER, split_cloud_cover, gran-orb, granule-stub]
Index: []

In [29]:
return_df[return_df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
1  These data have been created by the Department...   

                                           alternate  \
1  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                    category   category__gn_description  cloud_cover csw_type  \
1  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0  dataset   

                                    csw_wkt_geometry                 date  \
1  POLYGON((-6.17931146696 49.4453444507,-6.17931...  2020-08-10T11:33:31   

                                          detail_url    id  \
1  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...  9746   

                                            keywords  \
1  [analysis-ready-data, earth-observation, satel...   

                                            location owner__username  \
1  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

   popular_count  rating                   regions  share_count  \
1              2       0  [Europe, United Kingdom]            0   

   split_granule        srid subtype  \
1            NaN  EPSG:27700  raster   

                            supplemental_information  \
1  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                       thumbnail_url  \
1  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                               title   type  \
1  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                   uuid  split_granule.cloud_cover  \
1  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                  split_granule.name granule-ref orbit-ref  \
1  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

     ARCSI_CLOUD_COVER                       title_stub  \
1  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

  split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
1       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [30]:
return_df

abstract  \
0   These data have been created by the Department...   
1   These data have been created by the Department...   
2   These data have been created by the Department...   
3   These data have been created by the Department...   
4   These data have been created by the Department...   
5   These data have been created by the Department...   
6   These data have been created by the Department...   
7   These data have been created by the Department...   
8   These data have been created by the Department...   
9   These data have been created by the Department...   
10  These data have been created by the Department...   
11  These data have been created by the Department...   
12  These data have been created by the Department...   
13  These data have been created by the Department...   
14  These data have been created by the Department...   
15  These data have been created by the Department...   
16  These data have been created by the Department...   
17  These data have been created by the Department...   
18  These data have been created by the Department...   
19  These data have been created by the Department...   
20  These data have been created by the Department...   
21  These data have been created by the Department...   
22  These data have been created by the Department...   
23  These data have been created by the Department...   
24  These data have been created by the Department...   
25  These data have been created by the Department...   
26  These data have been created by the Department...   
27  These data have been created by the Department...   
28  These data have been created by the Department...   
29  These data have been created by the Department...   
30  These data have been created by the Department...   
31  These data have been created by the Department...   
32  These data have been created by the Department...   
33  These data have been created by the Department...   
34  These data have been created by the Department...   
35  These data have been created by the Department...   
36  These data have been created by the Department...   
37  These data have been created by the Department...   
38  These data have been created by the Department...   
39  These data have been created by the Department...   
40  These data have been created by the Department...   
41  These data have been created by the Department...   

                                            alternate  \
0   geonode:S2B_20200805_lat50lon684_T29UPR_ORB080...   
1   geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
2   geonode:S2B_20210721_lat51lon538_T29UQS_ORB080...   
3   geonode:S2B_20210718_lat50lon503_T30UUA_ORB037...   
4   geonode:S2B_20210721_lat51lon507_T30UUB_ORB080...   
5   geonode:S2B_20210718_lat50lon363_T30UVA_ORB037...   
6   geonode:S2B_20210718_lat51lon364_T30UVB_ORB037...   
7   geonode:S2B_20210718_lat52lon366_T30UVC_ORB037...   
8   geonode:S2B_20210718_lat53lon367_T30UVD_ORB037...   
9   geonode:S2B_20210721_lat54lon368_T30UVE_ORB080...   
10  geonode:S2B_20210721_lat55lon37_T30UVF_ORB080_...   
11  geonode:S2B_20210721_lat55lon371_T30UVG_ORB080...   
12  geonode:S2B_20190226_lat50lon223_T30UWA_ORB137...   
13  geonode:S2B_20190226_lat51lon222_T30UWB_ORB137...   
14  geonode:S2B_20210718_lat52lon22_T30UWC_ORB037_...   
15  geonode:S2B_20210718_lat53lon219_T30UWD_ORB037...   
16  geonode:S2B_20210718_lat54lon217_T30UWE_ORB037...   
17  geonode:S2A_20210723_lat55lon215_T30UWF_ORB037...   
18  geonode:S2A_20210723_lat55lon213_T30UWG_ORB037...   
19  geonode:S2B_20190226_lat50lon084_T30UXA_ORB137...   
20  geonode:S2B_20190226_lat51lon08_T30UXB_ORB137_...   
21  geonode:S2B_20190226_lat52lon075_T30UXC_ORB137...   
22  geonode:S2B_20190226_lat53lon071_T30UXD_ORB137...   
23  geonode:S2B_20190226_lat54lon066_T30UXE_ORB137...   
24  geonode:S2B_20190226_lat55lon061_T30UXF_ORB137...   
25  geonode:S2A_20200807_lat55lon055_T30UXG_ORB037...   
26  geonode:S2B_20210722_lat50lon056_T30UYA_ORB094... 